In [2]:
import wsi_preprocessing as pp
import os
import json
import shutil
import pandas as pd
import torch
import torch.nn as nn
from torchvision import models, transforms
from PIL import Image
from tqdm import tqdm
from torchvision.models import ResNet50_Weights
import random

In [3]:
def create_average_embedding(base_dir, case_id, slide_name):
    case_dir = os.path.join(base_dir, case_id)
    biospecimen_dir = os.path.join(case_dir, "Biospecimen")
    tiles_dir = os.path.join(biospecimen_dir, "Tiles")
    metadata_path = os.path.join(case_dir, "aggregated_data", f'{case_id}_data.json')

    tile_csv_path = None

    if not os.path.exists(tiles_dir):
        print(f"No tiles directory found for case {case_id}.")
        return None
    
    for file in os.listdir(tiles_dir):
        if file.endswith('filtered_tiles.csv') and slide_name in file:
            tile_csv_path = os.path.join(tiles_dir, file)
            break

    if not tile_csv_path:
        print(f"No valid tile CSV found for slide {slide_name} in case {case_id}.")
        return
    
    # randomly select a subset of tiles for faster processing
    tile_df = pd.read_csv(tile_csv_path)
    tile_paths = tile_df['tile_path'].dropna().tolist()
    tile_paths = random.sample(tile_paths, min(200, len(tile_paths)))

    if len(tile_paths) == 0:
        print(f"No tiles found in {tile_csv_path}.")
        return
    
    # Load pre-trained ResNet model
    device = 'cuda' if torch.cuda.is_available() else 'cpu'
    resnet = models.resnet50(weights=ResNet50_Weights.DEFAULT)
    resnet.fc = nn.Identity()  # Remove classification head to extract embeddings
    resnet = resnet.to(device)
    resnet.eval()

    # Image preprocessing pipeline
    preprocess = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
    ])

    # Calculate embeddings for all tiles
    embeddings = []
    for tile_path in tqdm(tile_paths, desc=f"Processing tiles for slide {slide_name}", unit="tile", leave=False):
        try:
            tile_full_path = os.path.join(tiles_dir, tile_path)  # Full path to tile
            image = Image.open(tile_full_path).convert('RGB')
            input_tensor = preprocess(image).unsqueeze(0).to(device)  # Add batch dimension
            
            with torch.no_grad():
                embedding = resnet(input_tensor).squeeze(0)  # Remove batch dimension
            embeddings.append(embedding)
        except Exception as e:
            print(f"Error processing tile {tile_path} in case {case_id}: {e}")
    
    # Compute the average embedding
    if len(embeddings) > 0:
        avg_embedding = torch.stack(embeddings).mean(dim=0).cpu().tolist()
    else:
        print(f"No embeddings generated for slide {slide_name} in case {case_id}.")
        return
    
    print(f"Average embedding for slide {slide_name} in case {case_id}: {avg_embedding}")
    return avg_embedding

def create_WSI_embeddings(base_dir="cases"):
    case_dirs = [d for d in os.listdir(base_dir) if os.path.isdir(os.path.join(base_dir, d))]

    for case_id in case_dirs:
        case_dir = os.path.join(base_dir, case_id)
        biospecimen_dir = os.path.join(case_dir, "Biospecimen")
        metadata_path = os.path.join(case_dir, "aggregated_data", f'{case_id}_data.json')

        if not os.path.exists(metadata_path):
            print(f"No metadata found for case {case_id}, skipping...")
            continue
        
        with open(metadata_path, 'r') as f:
            case_metadata = json.load(f)
        
        biospecimen_data = case_metadata.get('biospecimen', {}).get('biospecimen_data', [])

        # Collect svs image file names from JSON metadata file
        for sample in biospecimen_data:
            if sample['sample_type'] == "Primary Tumor":
                for slide in sample.get('slides', []):
                    image_name = slide['image_file_name']
                    embedding = create_average_embedding(base_dir, case_id, image_name)
                    slide['embedding'] = embedding
        
        with open(metadata_path, 'w') as f:
            json.dump(case_metadata, f, indent=4)
        print(f"Embeddings added for case {case_id} in the metadata.")

In [4]:
def preprocess_WSI_slides(base_dir="cases", hard_reset=False):
    case_dirs = [d for d in os.listdir(base_dir) if os.path.isdir(os.path.join(base_dir, d))]
    general_metadata_dir = os.path.join(base_dir, "GENERAL_METADATA")
    os.makedirs(general_metadata_dir, exist_ok=True)
    
    if "GENERAL_METADATA" in case_dirs:
        case_dirs.remove("GENERAL_METADATA")

    for case_id in case_dirs:
        case_dir = os.path.join(base_dir, case_id)
        biospecimen_dir = os.path.join(case_dir, "Biospecimen")
        metadata_path = os.path.join(case_dir, "aggregated_data", f'{case_id}_data.json')

        if not os.path.exists(metadata_path):
            print(f"No metadata found for case {case_id}, skipping...")
            continue
        
        with open(metadata_path, 'r') as f:
            case_metadata = json.load(f)
        
        # Check for Tiles.part
        tiles_part_dir = os.path.join(biospecimen_dir, 'Tiles.part')
        if os.path.exists(tiles_part_dir):
            shutil.rmtree(tiles_part_dir)
            print(f"Partially downloaded directory {tiles_part_dir} and its contents removed successfully.")

        # If Tiles exists, skip
        tiles_dir = os.path.join(biospecimen_dir, 'Tiles')
        if os.path.exists(tiles_dir):
            if hard_reset:
                shutil.rmtree(tiles_dir)
            else:
                print(f"Skipping case {case_id} because 'Tiles' directory already exists.")
                continue

        slides_to_process = []
        slide_names_to_process = []
        
        biospecimen_data = case_metadata.get('biospecimen', {}).get('biospecimen_data', [])
        
        # Collect svs image file names from JSON metadata file
        for sample in biospecimen_data:
            if sample['sample_type'] == "Primary Tumor":
                for slide in sample.get('slides', []):
                    slide_resolution_level = slide['resolution_level']
                    # make sure the slide is at least level 3 resolution
                    if slide_resolution_level >= 3:
                        image_name = slide['image_file_name']
                        slide_path = os.path.join(biospecimen_dir, image_name)
                        if os.path.exists(slide_path):
                            slides_to_process.append(slide_path)
                            slide_names_to_process.append(image_name)
                            for file in os.listdir(os.getcwd()):
                                # check for garbage files
                                if image_name in file:
                                    file_path = os.path.join(os.getcwd(), file)
                                    if os.path.isdir(file_path):
                                        shutil.rmtree(file_path, ignore_errors=True)
                                        print(f"Removed directory: {file_path}")
                                    elif os.path.isfile(file_path):
                                        os.remove(file_path)
                                        print(f"Removed file: {file_path}")
                        else:
                            print(f"Slide {image_name} not found for case {case_id}")
        
        if not slides_to_process:
            print(f"No Primary Tumor slides found for case {case_id}")
            continue
        
        os.makedirs(tiles_part_dir, exist_ok=True)

        slide_csv_path = os.path.join(tiles_part_dir, 'slides_mpp_otsu.csv')
        consolidated_csv_path = os.path.join(tiles_part_dir, 'consolidated.csv')
        tiles_filter_path = os.path.join(tiles_part_dir, 'tiles_filter.csv')
        filtered_tiles_path = os.path.join(tiles_part_dir, 'filtered_tiles.csv')
        
        # Commence tile cutting for current case
        pp.save_slides_mpp_otsu(slides_to_process, slide_csv_path)
        
        try:
            pp.run_tiling(
                slide_csv=slide_csv_path,
                consolidated_csv=consolidated_csv_path
            )
        except Exception as e:
            print(f"Exception during tiling for case {case_id}: {e}")
        
        pp.calculate_filters(
            slide_csv_path,
            "",
            tiles_filter_path
        )

        # Move generated files to appropriate folders
        for file in os.listdir(os.getcwd()):
            if "TCGA" in file and ".svs" in file:
              old_path = os.path.join(os.getcwd(), file)
              new_path = os.path.join(tiles_part_dir)
              
              # Print paths for debugging
              print(f"Attempting to move: {old_path} to {new_path}")
              
              try:
                  shutil.move(old_path, new_path)
                  print(f"Moved {file} successfully.")
              except Exception as e:
                  print(f"Failed to move {file}: {e}")

        for slide_name in slide_names_to_process:
            filters_csv_path = None
            for file in os.listdir(tiles_dir):
                if file.endswith("filters_cleanup.csv") and slide_name in file:
                    filters_csv_path = os.path.join(tiles_dir, file)
                    break

            if not filters_csv_path:
                print(f"No filters_cleanup.csv found for slide {slide_name} in case {case_id}.")
                continue

            df = pd.read_csv(filters_csv_path)
            filtered_df = df[df['bg_otsu'].notnull()]
            filtered_tiles_path = filters_csv_path.replace("filters_cleanup.csv", "filtered_tiles.csv")
            filtered_df.to_csv(filtered_tiles_path, index=False)

        if os.path.exists(tiles_part_dir):
            shutil.move(tiles_part_dir, tiles_dir)
            print(f"Renamed {tiles_part_dir} to {tiles_dir}")

        print(f"Processing complete for case {case_id}")

Error: Unable to rename the directory. Error: [WinError 2] The system cannot find the file specified


In [6]:
if __name__=='__main__':
  preprocess_WSI_slides("cases_TEST_TRAIN_100", False)
  create_WSI_embeddings("cases_TEST_TRAIN_100")                     

No Primary Tumor slides found for case 03efbc94-a43d-4db0-9377-e397348430a6
Skipping case 127f738d-afa1-42f6-a9a0-f33806667b84 because 'Tiles' directory already exists.
Skipping case 13eff2e5-e33a-485f-9ba4-8a7ccb3c7528 because 'Tiles' directory already exists.
Skipping case 14c13b05-abfe-472e-83a9-b28f60e58ad8 because 'Tiles' directory already exists.
Skipping case 14efca0c-882d-4fba-b15c-64af6e213b80 because 'Tiles' directory already exists.
Skipping case 1ad0b9b9-7ded-4281-b114-9dcc6138c037 because 'Tiles' directory already exists.
Skipping case 269e8ca8-722d-449b-ace1-6545bd72bdd6 because 'Tiles' directory already exists.
Skipping case 28033279-cc74-4775-afdf-2497f6ddb55c because 'Tiles' directory already exists.
Skipping case 2c0a725a-e829-4d84-89d9-d0d47f6cfa37 because 'Tiles' directory already exists.
Skipping case 2c9996bb-af6e-4424-881a-e81b9c9aeb78 because 'Tiles' directory already exists.
Skipping case 381cf7f3-cd7b-4660-8175-ff8062f7bf78 because 'Tiles' directory already ex

Average embedding for slide TCGA-AA-3562-01A-01-BS1.2bc37a71-647d-4e7e-9e3a-12191942a051.svs in case 127f738d-afa1-42f6-a9a0-f33806667b84: [0.011767884716391563, 0.12412942945957184, 0.007070085033774376, 0.0002604127221275121, 0.012880899012088776, 0.008400600403547287, 1.5915981531143188, 0.018007075414061546, 0.029957246035337448, 0.03753926604986191, 0.03373737260699272, 0.13205039501190186, 0.003609569277614355, 0.009052762761712074, 0.05986911430954933, 0.005944245494902134, 0.35085365176200867, 0.022362565621733665, 0.005457451567053795, 0.004284204915165901, 0.02003750391304493, 0.013905196450650692, 0.10903486609458923, 0.14257410168647766, 0.012017999775707722, 0.0019520403584465384, 0.0022975436877459288, 0.01119594182819128, 0.02569863386452198, 0.030234217643737793, 0.02842343971133232, 0.005810542032122612, 0.0019138673087581992, 0.015647374093532562, 0.012979925610125065, 0.0020587053149938583, 0.049554720520973206, 0.07569091022014618, 0.14802560210227966, 0.01774623431

Average embedding for slide TCGA-AA-3562-01A-02-BS2.545d3c6e-ca91-4f6a-9011-0bdbd41ef0cb.svs in case 127f738d-afa1-42f6-a9a0-f33806667b84: [0.007769031450152397, 0.1138588935136795, 0.006835990585386753, 0.0012997158337384462, 0.008736592717468739, 0.008657587692141533, 1.5207890272140503, 0.018703226000070572, 0.02822887897491455, 0.018588388338685036, 0.026095574721693993, 0.07466892898082733, 0.00863133929669857, 0.011973722837865353, 0.0683598667383194, 0.006142130587249994, 0.2684672176837921, 0.02733226865530014, 0.003191546304151416, 0.002960314741358161, 0.018085796386003494, 0.011961590498685837, 0.1240203008055687, 0.14723673462867737, 0.01847199536859989, 0.00229085935279727, 0.0018831841880455613, 0.014579527080059052, 0.01431250013411045, 0.037102531641721725, 0.03505365550518036, 0.010058270767331123, 0.00226734415628016, 0.006888986099511385, 0.008094835095107555, 0.004162587225437164, 0.051953501999378204, 0.11930453032255173, 0.12360534816980362, 0.02567492425441742, 0

Average embedding for slide TCGA-AD-6888-01A-01-TS1.e7e6ffce-c563-44ed-9483-ef7c37418b06.svs in case 13eff2e5-e33a-485f-9ba4-8a7ccb3c7528: [0.006476451177150011, 0.20123665034770966, 0.013551226817071438, 0.00014306779485195875, 0.005987417884171009, 0.041376784443855286, 2.078021764755249, 0.008721346035599709, 0.03308931738138199, 0.03230348229408264, 0.02813234180212021, 0.20980441570281982, 0.025605374947190285, 0.003659256035462022, 0.044049762189388275, 0.012945149093866348, 0.16002552211284637, 0.03186246007680893, 0.009386654943227768, 0.006865759380161762, 0.05972651392221451, 0.02605110965669155, 0.17358484864234924, 0.5303886532783508, 0.01662755198776722, 0.0024834289215505123, 0.005053191911429167, 0.012780698947608471, 0.007481204811483622, 0.05005877465009689, 0.023429811000823975, 0.12044017761945724, 0.00582878990098834, 0.0013864642241969705, 0.048120804131031036, 0.0006756319780834019, 0.06471353769302368, 0.08908302336931229, 0.0657285749912262, 0.02341485768556595,

Average embedding for slide TCGA-G4-6310-01A-01-BS1.07fd261c-fc73-43a5-b1f4-49b83e5f2ad4.svs in case 14c13b05-abfe-472e-83a9-b28f60e58ad8: [0.012619183398783207, 0.2678149342536926, 0.013241542503237724, 0.001227221917361021, 0.003646469907835126, 0.1039692685008049, 1.979705810546875, 0.017763914540410042, 0.03224961832165718, 0.0318169891834259, 0.03787706792354584, 0.19780424237251282, 0.015691537410020828, 0.007653315085917711, 0.03435920551419258, 0.011666430160403252, 0.18612432479858398, 0.03216787055134773, 0.007775264326483011, 0.010314013808965683, 0.020158963277935982, 0.021740417927503586, 0.12177535891532898, 0.6670690178871155, 0.03457929193973541, 0.0021045345347374678, 0.00457014050334692, 0.008829284459352493, 0.017143918201327324, 0.11851000040769577, 0.030811622738838196, 0.06666675209999084, 0.0019989542197436094, 0.009482154622673988, 0.06132185459136963, 0.00026710398378781974, 0.13276731967926025, 0.10369742661714554, 0.10484672337770462, 0.23460054397583008, 0.0

...

Average embedding for slide TCGA-AZ-6608-01A-01-BS1.c984f302-0ba8-4a23-8a27-455d29f01730.svs in case f1e6ce83-b4a0-4643-8e8e-a1ef8a158a27: [0.0052675483748316765, 0.33524632453918457, 0.018459510058164597, 0.00016972444427665323, 0.006382727064192295, 0.06896486133337021, 1.9376144409179688, 0.005023219157010317, 0.03869820386171341, 0.005744314286857843, 0.09178950637578964, 0.16264492273330688, 0.005838098004460335, 0.0042433845810592175, 0.04748640954494476, 0.017384108155965805, 0.15639165043830872, 0.02098456397652626, 0.012056215666234493, 0.007291766349226236, 0.0198653694242239, 0.013111394830048084, 0.12502892315387726, 0.2551402151584625, 0.022330451756715775, 0.0018887859769165516, 0.0024517797864973545, 0.028316712006926537, 0.008775409311056137, 0.05119561776518822, 0.01870637573301792, 0.21253985166549683, 0.0030139214359223843, 0.010171848349273205, 0.11033106595277786, 0.0018165665678679943, 0.12635298073291779, 0.05392519012093544, 0.049052972346544266, 0.0151711227372

Average embedding for slide TCGA-AZ-6608-01A-01-TS1.8b47ab2b-d642-4fcb-b26a-055e33495b00.svs in case f1e6ce83-b4a0-4643-8e8e-a1ef8a158a27: [0.009603699669241905, 0.34172534942626953, 0.01035581436008215, 0.00030332739697769284, 0.0023217301350086927, 0.07060976326465607, 2.0517749786376953, 0.00724573852494359, 0.033892758190631866, 0.006950211711227894, 0.11163046211004257, 0.14468301832675934, 0.0027075253892689943, 0.005282221361994743, 0.04563508182764053, 0.015118603594601154, 0.20565371215343475, 0.025521479547023773, 0.013188538141548634, 0.007395033724606037, 0.023162715137004852, 0.012892186641693115, 0.14972470700740814, 0.306440532207489, 0.01685042679309845, 0.006129879504442215, 0.0019211951876059175, 0.01631063036620617, 0.00786413624882698, 0.09420401602983475, 0.03106137365102768, 0.12435325980186462, 0.00339684565551579, 0.006237576715648174, 0.10120318084955215, 0.003347638063132763, 0.1504266858100891, 0.06327786296606064, 0.05134714022278786, 0.02859531342983246, 0.

Average embedding for slide TCGA-AA-3814-01A-01-BS1.10a3eaf7-1dd1-466d-b306-acab6b4a6963.svs in case f38d49b7-6cad-4460-abd0-3685a3b2d941: [0.005891906563192606, 0.07689838111400604, 0.004011533688753843, 0.000602759188041091, 0.023058705031871796, 0.006825115531682968, 1.2828422784805298, 0.006986516527831554, 0.02063651755452156, 0.0214886162430048, 0.060958560556173325, 0.12405277043581009, 0.008588727563619614, 0.013467572629451752, 0.110536128282547, 0.005526232533156872, 0.32877448201179504, 0.015506161376833916, 0.0029865996912121773, 0.0012308621080592275, 0.015414264984428883, 0.022920718416571617, 0.10364624857902527, 0.05349339544773102, 0.01124864537268877, 0.0009731495520099998, 0.002338971709832549, 0.010454142466187477, 0.013595202937722206, 0.04117235168814659, 0.025517214089632034, 0.01178087666630745, 0.0024397517554461956, 0.013603158295154572, 0.006253455765545368, 0.0016968277050182223, 0.016691146418452263, 0.0622851736843586, 0.15066780149936676, 0.01617100089788

Average embedding for slide TCGA-AA-3814-01A-01-TS1.c72a49a0-eeb1-4b19-8f31-08f1a521a8dc.svs in case f38d49b7-6cad-4460-abd0-3685a3b2d941: [0.007649490609765053, 0.10344546288251877, 0.003768183523789048, 0.0004947406705468893, 0.009910430759191513, 0.023230677470564842, 1.3559963703155518, 0.005121663212776184, 0.020590979605913162, 0.03219079598784447, 0.05515724793076515, 0.15607021749019623, 0.017758391797542572, 0.019715433940291405, 0.09553024172782898, 0.005194306373596191, 0.3109319806098938, 0.015424791723489761, 0.004325963091105223, 0.003684547496959567, 0.025290515273809433, 0.022119559347629547, 0.13428005576133728, 0.08178756386041641, 0.014557991176843643, 0.0006967346416786313, 0.00294575490988791, 0.00863352045416832, 0.01621387153863907, 0.024240273982286453, 0.0368453674018383, 0.008635038509964943, 0.0039043722208589315, 0.012884695082902908, 0.016658341512084007, 0.001998130464926362, 0.03626706451177597, 0.031182652339339256, 0.16881540417671204, 0.029399301856756

Average embedding for slide TCGA-AA-3556-01A-01-BS1.6c414ca3-3254-4af5-a3a6-5ac24a643f02.svs in case fd16b634-2e04-44a3-862d-fb03cd73c057: [0.005449718330055475, 0.17918233573436737, 0.005573747213929892, 0.001192270196042955, 0.008097517304122448, 0.01326009351760149, 1.281333565711975, 0.013687278144061565, 0.025677291676402092, 0.0374189168214798, 0.021335046738386154, 0.19213458895683289, 0.02152489498257637, 0.023819614201784134, 0.0558466911315918, 0.005754929967224598, 0.37553340196609497, 0.030394548550248146, 0.003995542414486408, 0.0029321706388145685, 0.029376866295933723, 0.018595276400446892, 0.13235267996788025, 0.1128358244895935, 0.012438392266631126, 0.0014960109256207943, 0.009629512205719948, 0.011007620953023434, 0.022633308544754982, 0.06338606774806976, 0.053767457604408264, 0.007539522834122181, 0.001824286300688982, 0.0036794119514524937, 0.011149019934237003, 0.003855206770822406, 0.07964792847633362, 0.09197968244552612, 0.1414908766746521, 0.07559709250926971